# トレンドレコメンドAPI（仮）のテスト

## 概要

- 世間で話題になっているトレンドを抽出し、トレンドに関連した商品を自動抽出する
- 使用したAPI （TwitterAPI, NewsAPI, 楽天API）

## 処理の流れ

1. 以下のいずれかの方法により、トレンドワードを取得する
- GoogleトレンドのWebページをクローリング・スクレイピングし、Google検索で急上昇中のワードを取得する
- TwitterAPIを使用し、Twitterでトレンドになっているワードを取得する
- NewsAPIを使用し、国内ニュースでトレンドになっているニュースを取得する（これはワードではなく、ニュース記事を取得）
<br>
※ 各処理で必要となる処理は関数化済みだが、今回はGoogleトレンドのパターンで実験する


2. トレンドワードに関連するニュース記事をNewsAPIを使用して取得する
- 取得したトレンドワードでニュース記事を検索する
- ニュース記事をタイトルと概要を取得する（本文取得はAPIではできない）

3. トレンドワードとニュース記事（複数）を一つのテキストにまとめる
4. 楽天APIを使用し、楽天ブックスで販売する書籍のタイトル・著者・概要を取得する
- 一度に楽天APIで取得できる商品数には制限がある為、事前にAPIを一日叩き続けて取得できた10万件近い書籍のデータを使用する
- 書籍データはpandasのデータとして保持し、pickleファイル化しておく（実際はDBに保存しておきたい）

5. 4のタイトル・著者・概要を一つのテキストにまとめる

6. 3と5をMecabで形態素解析し、名詞だけを取得する

7. TFIDFのベクトル化して、トレンドワードのテキストに一番類似する商品テキストをCOS類似度で取得する

## 以下、処理内容

In [1]:
# 必要なライブラリをインストール（AWSで環境をゼロから作り直す時必要）
# !pip install newsapi-python
# !pip install twitter
# !pip install selenium
# !pip install feedparser

### 前処理

In [2]:
# 各APIで必要なライブラリをインポート
from newsapi import NewsApiClient
from twitter import *

In [3]:
# その他、必要なライブラリをインポート
import datetime
import re
from selenium import webdriver
import time
import feedparser
import random

In [4]:
# API_KEYの設定ファイルを読み込み
# ※ APIを使用する為に必要となるキーとパスをまとめた設定ファイルを別途作成し、それを呼び出している
import configparser
config = configparser.ConfigParser()
config.read('config.ini')

['config.ini']

### news_api

In [5]:
# news_apiから、検索したキーワードに関連するニュース情報を返す関数
def keyword_news_search(\
                         api_key = config['NEWS_API']['KEY'],\
                         search_word = '', \
                         start_date = datetime.datetime.now().strftime('%Y-%m-%d'),\
                         end_date = datetime.datetime.now().strftime('%Y-%m-%d'), \
                         sort_type = 'popularity'\
                        ):
    
    # news_apiを初期化
    news_api_search = NewsApiClient(api_key=config['NEWS_API']['KEY'])
    
    # search_wordで指定したキーワードに関するニュースを検索する
    result_search_news = news_api_search.get_everything(qintitle=search_word, from_param=start_date ,to=end_date, sort_by=sort_type)
    
    return result_search_news

In [6]:
sample_news = keyword_news_search(search_word = 'LG')
sample_news
# 検索ワードによっては、件数が少ない場合がある。ニュース検索は複数回必要そう。。

{'status': 'ok',
 'totalResults': 39,
 'articles': [{'source': {'id': 'engadget', 'name': 'Engadget'},
   'author': 'Eric Chan',
   'title': 'LG 计划外包更多低阶和中阶手机',
   'description': 'LG 再一次的重组旗下手机部门，他们向 Reuters 确认了会增加外包低阶和中阶手机的设计和生产的数量，自己就会专注到高阶产品。',
   'url': 'https://cn.engadget.com/lg-smartphone-outsourcing-040116895.html',
   'urlToImage': 'https://s.yimg.com/os/creatr-uploaded-images/2020-12/b6740760-3901-11eb-b3da-d8e106e9eadf',
   'publishedAt': '2020-12-08T04:01:16Z',
   'content': None},
  {'source': {'id': None, 'name': '36kr.com'},
   'author': None,
   'title': 'LG电子重组手机部门以提高中低端智能手机外包生产',
   'description': 'LG电子周一称其已对手机部门进行重组，此举旨在增加中低端智能手机的外包生产。分析师认为，这意味着该公司试图削减成本，并与中国的对手展开竞争。LG电子的一位发言人表示，该公司的移动通信业务已经连续22个季度出现运营亏损，并称其为原始设计制造（ODM）设立了一个新的管理头衔。所谓“原始设计制造”是指LG电子将智能手机的设计和制造外包，随后将自己的标签贴在这些产品上。（新浪科技）',
   'url': 'https://36kr.com/newsflashes/1001295405486600',
   'urlToImage': 'https://img.36krcdn.com/20191024/v2_1571894049839_img_jpg',
   'publishedAt': '2020-12-08T00:10:21Z',
   'co

In [7]:
# news_apiから、トップニュース情報を返す関数
def headlines_news(\
                         api_key = config['NEWS_API']['KEY'],\
                         target_category = 'entertainment', \
                         target_country = 'jp'
                        ):
    
    # news_apiを初期化
    news_api_headlines = NewsApiClient(api_key=config['NEWS_API']['KEY'])
    
    # 指定したオプションに従ったトップニュースを検索する     
    # Possible options: business entertainment general health science sports technology . 
    # Note: you can't mix this param with the sources param.
    result_headlines_news = news_api_headlines.get_top_headlines(category=target_category, country=target_country)
    
    return result_headlines_news

In [8]:
sample2 = headlines_news(target_category='business')
sample2

{'status': 'ok',
 'totalResults': 70,
 'articles': [{'source': {'id': None, 'name': 'Itmedia.co.jp'},
   'author': '迎悟，ITmedia',
   'title': 'ドコモの新プラン「ahamo」は携帯料金の常識を変えた？ ワイモバ・UQとの違いとは - ITmedia',
   'description': 'ついに出そろった携帯大手3社の新料金プランを比較。「ahamo」が携帯業界にどんな影響を与えるか考察する。',
   'url': 'https://www.itmedia.co.jp/news/articles/2012/08/news098.html',
   'urlToImage': 'https://image.itmedia.co.jp/news/articles/2012/08/cover_news098.jpg',
   'publishedAt': '2020-12-08T05:30:00Z',
   'content': 'NTT123ahamo298020GBWeb\r\nNTTKDDIUQ mobile20GB3980VY!mobile20GB4480203\r\n3ahamo\r\nahamo2\r\n3\r\n320GB50GB80001GB500057GB\r\nahamo3UQ mobileV3480ahamo2980V3020ahamo5\r\n25GahamoSIM\r\n223ahamoahamo2\r\nahamo\r\nahamo\r… [+78 chars]'},
  {'source': {'id': None, 'name': 'Nikkei.com'},
   'author': 'Nikkei Inc.',
   'title': '[FT]Uber、自動運転子会社を売却 自社開発を断念 - 日本経済新聞',
   'description': '日本経済新聞の電子版。日経や日経ＢＰの提供する経済、企業、国際、政治、マーケット、情報・通信、社会など各分野のニュース。ビジネス、マネー、IT、スポーツ、住宅、キャリアなどの専門情報も満載。',
   'url': 'https://www.nik

### twitter_api

In [9]:
# twitter_apiから、ツイートトレンドの単語を返す関数
def twitter_trends_search(\
                          CK = config['TWITTER_API']['CONSUMER_KEY'],\
                          CS = config['TWITTER_API']['CONSUMER_SECRET'],\
                          AT = config['TWITTER_API']['ACCESS_TOKEN'],\
                          AS = config['TWITTER_API']['ACCESS_TOKEN_SECRET'],\
                          area_id = 23424856\
                         ):
    
     # twitter_apiを初期化
    twitter_api_trends = Twitter(auth = OAuth(AT,AS,CK,CS))
        
     # 指定したエリアのツイッタートレンドを検索する
    twitter_trends_results = twitter_api_trends.trends.place(_id = area_id)
                    
    return twitter_trends_results

In [10]:
# トレンドのキーワードを加工して、リストに格納する
sample3 = twitter_trends_search()
sample3

[{'trends': [{'name': '学力低下',
    'url': 'http://twitter.com/search?q=%E5%AD%A6%E5%8A%9B%E4%BD%8E%E4%B8%8B',
    'promoted_content': None,
    'query': '%E5%AD%A6%E5%8A%9B%E4%BD%8E%E4%B8%8B',
    'tweet_volume': 28682},
   {'name': '市議ら意見交換会',
    'url': 'http://twitter.com/search?q=%E5%B8%82%E8%AD%B0%E3%82%89%E6%84%8F%E8%A6%8B%E4%BA%A4%E6%8F%9B%E4%BC%9A',
    'promoted_content': None,
    'query': '%E5%B8%82%E8%AD%B0%E3%82%89%E6%84%8F%E8%A6%8B%E4%BA%A4%E6%8F%9B%E4%BC%9A',
    'tweet_volume': 23949},
   {'name': 'プリティ5',
    'url': 'http://twitter.com/search?q=%E3%83%97%E3%83%AA%E3%83%86%E3%82%A35',
    'promoted_content': None,
    'query': '%E3%83%97%E3%83%AA%E3%83%86%E3%82%A35',
    'tweet_volume': 17944},
   {'name': 'Wi-Fi電磁波',
    'url': 'http://twitter.com/search?q=Wi-Fi%E9%9B%BB%E7%A3%81%E6%B3%A2',
    'promoted_content': None,
    'query': 'Wi-Fi%E9%9B%BB%E7%A3%81%E6%B3%A2',
    'tweet_volume': 26820},
   {'name': '販売休止',
    'url': 'http://twitter.com/search?q=%E8%B2%A9%E5%A3

In [11]:
# twitter_trends_list = []
# for location in sample3:
#         for trend in location["trends"]:
#              twitter_trends_list.append(re.sub('#', "", trend["name"]))

# twitter_trends_list

In [12]:
# twitter_apiから、検索したキーワードに関連するツイートを返す関数
def twitter_search(\
                          CK = config['TWITTER_API']['CONSUMER_KEY'],\
                          CS = config['TWITTER_API']['CONSUMER_SECRET'],\
                          AT = config['TWITTER_API']['ACCESS_TOKEN'],\
                          AS = config['TWITTER_API']['ACCESS_TOKEN_SECRET'],\
                          search_keyword = 'twitter',\
                          search_lang = 'ja',\
                          search_type = 'mixed',\
                          search_count = 100\
                         ):
    
     # twitter_apiを初期化
    twitter_api_search = Twitter(auth = OAuth(AT,AS,CK,CS))
        
     # 指定したエリアのツイッタートレンドを検索する
    search_results = twitter_api_search.search.tweets(q=search_keyword, lang=search_lang, result_type=search_type, count=search_count)
                    
    return search_results

In [13]:
sample4 = twitter_search(search_keyword='全国高等学校サッカー選手権大会')
sample4

{'statuses': [{'created_at': 'Mon Dec 07 06:11:33 +0000 2020',
   'id': 1335829278374592512,
   'id_str': '1335829278374592512',
   'text': '第99回全国高等学校サッカー選手権大会チケット販売概要のお知らせ #jfa https://t.co/AvINJ5e6Ah',
   'truncated': False,
   'entities': {'hashtags': [{'text': 'jfa', 'indices': [33, 37]}],
    'symbols': [],
    'user_mentions': [],
    'urls': [{'url': 'https://t.co/AvINJ5e6Ah',
      'expanded_url': 'https://bit.ly/2VNz1LA',
      'display_url': 'bit.ly/2VNz1LA',
      'indices': [38, 61]}]},
   'metadata': {'result_type': 'popular', 'iso_language_code': 'ja'},
   'source': '<a href="https://dlvrit.com/" rel="nofollow">dlvr.it</a>',
   'in_reply_to_status_id': None,
   'in_reply_to_status_id_str': None,
   'in_reply_to_user_id': None,
   'in_reply_to_user_id_str': None,
   'in_reply_to_screen_name': None,
   'user': {'id': 72914344,
    'id_str': '72914344',
    'name': '日本サッカー協会',
    'screen_name': 'JFA',
    'location': '東京都文京区本郷三丁目',
    'description': '日本サッカー協会(JFA)公式アカウントで

In [14]:
# for i in range(len(sample4["statuses"])):
#     print(sample4["statuses"][i]["text"])

### Googleトレンド（クローリング・スクレイピング）

In [15]:
def google_trends_search(\
                        base_url = 'https://trends.google.co.jp/trends/trendingsearches/realtime',\
                        search_geo = 'JP',\
                        search_category = 'all',
                        ):
    
    # 検索するURLを作成する
    url = '{i}?geo={j}&category={k}'.format(i=base_url, j=search_geo, k=search_category)
    
    # ブラウザを開く
    driver = webdriver.Chrome()
    
    # Googleトレンドの検索TOP画面を開く （表示サイズも指定しておく）
    driver.get(url)
    driver.set_window_size(2500,1000)
    
    # 2〜4秒間、ページが開かれるのを待つ
    time.sleep(random.randint(2,4))
    
    # TOP画面より、必要な要素のデータを取得する
    trends_keywords = driver.find_elements_by_class_name('title')
    summary_text = driver.find_elements_by_class_name('summary-text')
    source_text = driver.find_elements_by_class_name('source-and-time')
        
    # 全ての要素が取得できた場合、処理を進める
    while bool(len(trends_keywords) == 0 or  len(summary_text) == 0 or len(source_text) == 0):
        time.sleep(10)
        trends_keywords = driver.find_elements_by_class_name('title')
        summary_text = driver.find_elements_by_class_name('summary-text')
        source_text = driver.find_elements_by_class_name('source-and-time')
    else:
        trends_keyword = []
        trends_abst = []
        inyo_url = []
        inyo_site = []
        for i in range(len(trends_keywords)):
            trends_keyword.append(trends_keywords[i].text)
            trends_abst.append(summary_text[i].text)
            inyo_url.append(summary_text[i].find_element_by_tag_name("a").get_attribute("href"))
            inyo_site.append(source_text[i].text.split()[0])
    
    # 各トレンドごとに詳細情報を取得する為、要素をクリックし必要なHTMLを表示させる（その為のクリックする要素を取得している）
    trend_click = driver.find_elements_by_class_name('feed-item')
    
    # 蓄積用のリストを用意しておく
    google_trend_news_list = []
    google_trend_words_list = []
    
    # トレンドごとに詳細情報を取得する為、要素をクリックし必要なHTMLを表示させる
    for trend in trend_click:
        trend.click()
        
        # 1秒間、ページが開かれるのを待つ
        time.sleep(1)
        
        # 引用ニュースを取得
        google_trend_news_tmp = driver.find_elements_by_class_name('item-title')
        google_trend_news = ''
        for news in google_trend_news_tmp:
            google_trend_news = google_trend_news + news.text
            
        # 関連ワードを取得
        google_trend_words_tmp = driver.find_elements_by_class_name('list')
        google_trend_words = google_trend_words_tmp[0].text.replace(" ","")
        
        # リストに追加
        google_trend_news_list.append(google_trend_news)
        google_trend_words_list.append(google_trend_words) 
            
    driver.quit()
    
    google_trend_data = {'goole_keyword': trends_keyword, 'google_abst': trends_abst, 'google_url': inyo_url, 'google_site': inyo_site, \
                        'google_news':google_trend_news_list, 'google_words':google_trend_words_list}
    
    return google_trend_data

In [16]:
sample5 = google_trends_search()

In [17]:
sample5

{'goole_keyword': ['ネスレ・ミロ • ネスレ日本 • ネスレ • ネスカフェ ドルチェグスト専用カプセル カフェオレ インテンソ (16杯分)',
  '築地銀だこ • 福袋 • たこめし • ホットランド',
  '内閣官房参与 • 西川公也 • 自由民主党 • 農林水産大臣',
  '環太平洋パートナーシップ協定 • 文在寅 • 大韓民国 • 地域的な包括的経済連携協定',
  'モスバーガー • 旭酒造 • 山田錦',
  'ジョン・レノン • ビートルズ • オノ・ヨーコ • ポール・マッカートニー',
  '村上佳菜子',
  'ナイツ • 羽生善治 • 藤井聡太 • 鈴木 福 • 日本放送協会 • 先崎学 • NHK BSプレミアム',
  '玉木雄一郎 • 国民民主党 • 伊藤孝恵 • 国民民主党代表選挙 • 参議院 •',
  '武藤 遊戯 • 遊☆戯☆王デュエルモンスターズ • 海馬 瀬人 • 風間 俊介',
  '京阪電気鉄道 • 京阪5000系電車 • 方向幕 • 中之島駅',
  '佐久田脩 • NCIS 〜ネイビー犯罪捜査班 • 星雲仮面マシンマン • 連続テレビ小説',
  '西浦颯大 • オリックス・バファローズ • 育成選手制度 • 特発性大腿骨頭壊死症',
  'NHK紅白歌合戦 • いきものがかり • 日本放送協会 • 山下 穂尊',
  'インド • アーンドラ・プラデーシュ',
  'ポケットモンスター • Pokémon GO • iOS • ポケモンボックス ルビー&サファイア'],
 'google_abst': ['「ミロ」再び販売休止に 注文は約7倍、「安定した供給の継続が困難」',
  '築地銀だこ「ぜったいお得な!! 福袋」が2021年も登場！ 1000円で最大2010円お得にたこ焼きが食べられるぞ！',
  '西川公也内閣官房参与が辞任意向 現金提供疑惑絡む',
  '韓国がＴＰＰ参加検討 文大統領が初めて言及',
  'モスバーガーと「獺祭」が初コラボ! ノンアルコールの甘酒シェイクが登場',
  'ジョン・レノンさん死去40年 「あの日そこにいた」BBC記者が振り返る',
  '村上佳菜子、父の写真公開に驚きの声続々「俳優さん？」「めっちゃイケメンですね～」',
  'ナイツ土屋が羽生善

### 英語ページの作成も同時に行う場合、GoogleCloudTranslateのAPIが動くようにすること（あと、GoogleTrendのクローリング処理も改良すること）

## 必要な処理は用意できたので、ここからレコメンドを作っていく。

In [81]:
google_trend_word = sample5['goole_keyword'][15].split(' • ')

In [82]:
google_trend_news = sample5['google_news'][15]

In [83]:
google_trend_words = sample5['google_words'][15]

In [84]:
google_trend_word

['ポケットモンスター', 'Pokémon GO', 'iOS', 'ポケモンボックス ルビー&サファイア']

In [85]:
google_trend_news

'...'

In [86]:
google_trend_words

'ポケモンgoログインできない\nポケモンgo不具合\nスポットライトアワー\nポケモンgo起動しない\nポケモンgo繋がらない\nポケモンgoツイッター\nポケモンgo障害\nポケモンgo開かない\nポケモンgoスポットライトアワー\nポケモンgo立ち上がらない\nポケモンgoログインできないリアルタイム\nポケモンgo通信障害\nポケモンgo障害リアルタイム\nポケモンgo不具合今\nポケモンgoリモートレイドパス\nポケモンgoサインインできない\nポケモンgo繋がらない今\nポケモンgoエラー\nポケモンgo不具合ツイッター\nポケモンgoレベル44\nポケモンgoつながらない\nポケモンgo不具合報告\nポケモンgoネットワークエラー\nポケモンgoアプリ\nポケモンgo起動しない今日'

#### トレンドワードに基づいて、関連ニュースを取得する

In [24]:
# 全トレンド ワードを使って、ニュースを検索したい場合のコード
# news_text = ''
# for google_word in google_trend_word:
#     time.sleep(1)
#     news_text_tmp = keyword_news_search(search_word = google_word)
#     for i in news_text_tmp['articles']:
#         news_text += (i['title'] +","+ i['description'])
#         print((i['title'] +","+ i['description']))

In [88]:
sample_news = keyword_news_search(search_word = google_trend_word[0])

In [89]:
news_text = ''
for i in sample_news['articles']:
    news_text += (i['title'] +","+ i['description'])

In [90]:
# ポケットモンスターという単語では、直近ニュース記事が見つからなかった模様（こんなこともある）
news_text

'『劇場版ポケットモンスター ココ』オンラインリアル脱出ゲームの開催を記念し、映画公式サイトにて無料で遊べる謎解き企画が開催,SCRAPは、映画『劇場版ポケットモンスター ココ』とコラボしたオンラインリアル脱出ゲーム“幻のポケモンの森からの脱出”の開催を記念して、映画公式サイトにて無料で遊べる謎解き企画を公開した。'

#### トレンドワードに基づいて、関連ツイートを取得する

In [91]:
twitter_text_tmp = twitter_search(search_keyword=google_trend_word[0], search_count = 10)
twitter_text_tmp

{'statuses': [{'created_at': 'Mon Dec 07 03:00:33 +0000 2020',
   'id': 1335781214678966274,
   'id_str': '1335781214678966274',
   'text': '＼めくってラッキー‼／\n『ポケットモンスター ソード・シールド』で受け取れる、おやめいミスドの #ラッキー がもらえちゃう、「#ラッキースクラッチカード」は1,000円（税込）ごとのお買い上げで1枚ゲットできます⭐… https://t.co/b65GsoF9My',
   'truncated': True,
   'entities': {'hashtags': [{'text': 'ラッキー', 'indices': [48, 53]},
     {'text': 'ラッキースクラッチカード', 'indices': [63, 76]}],
    'symbols': [],
    'user_mentions': [],
    'urls': [{'url': 'https://t.co/b65GsoF9My',
      'expanded_url': 'https://twitter.com/i/web/status/1335781214678966274',
      'display_url': 'twitter.com/i/web/status/1…',
      'indices': [109, 132]}]},
   'metadata': {'result_type': 'popular', 'iso_language_code': 'ja'},
   'source': '<a href="https://social.userlocal.jp/" rel="nofollow">Social Insight Post</a>',
   'in_reply_to_status_id': None,
   'in_reply_to_status_id_str': None,
   'in_reply_to_user_id': None,
   'in_reply_to_user_id_str': None,
   'in_reply_to_screen

In [92]:
# ツイッターで検索しちゃうと、
twitter_text = ''
for i in range(len(twitter_text_tmp["statuses"])):
    twitter_text += twitter_text_tmp["statuses"][i]["text"]

In [93]:
twitter_text

'＼めくってラッキー‼／\n『ポケットモンスター ソード・シールド』で受け取れる、おやめいミスドの #ラッキー がもらえちゃう、「#ラッキースクラッチカード」は1,000円（税込）ごとのお買い上げで1枚ゲットできます⭐… https://t.co/b65GsoF9Myオンラインリアル脱出ゲーム×\n劇場版ポケットモンスター ココ\n「幻のポケモンの森からの脱出」\n開催記念謎解き企画\n\nキミは、ポケモン映画公式サイトに仕掛けられた💡謎💡を解けるか⁉\n\nhttps://t.co/iizmCFStWL… https://t.co/E4QV8A0EsT4日連続！フォロー＆RTすると\n「ポケットモンスター ソードまたはシールド＋エキスパンションパス」が抽選であたる🎁\n\n1日1回チャレンジしてね！\n\n1.@misterdonut_jpをフォロー\n2.12/3 11:59迄にRT\n※… https://t.co/UBK4liWOKa【アニメでのガブリアス】\nポケットモンスターダイヤモンドパールからポケットモンスターXY(2014年1月現在)まで実は何らかの形でゲスト出演で登場していたりする。\n初登場はDP編第40話RT @famitsu: 『劇場版ポケットモンスター ココ』オンラインリアル脱出ゲームの開催を記念し、映画公式サイトにて無料で遊べる謎解き企画が開催 https://t.co/9WiHvBgt8O https://t.co/8KouDyXaDf『ポケットモンスター金・銀』: ［こおりのぬけみち］で拾うことができる［わざマシン］と［ひでんマシン］を両方答えよ。--完答15点 #poke_qJR線秋葉原駅、パノラマ秋葉原「劇場版ポケットモンスター ココ」#ココ #ポケモン映画 #ooh https://t.co/WonWi0Wacwさいたまスーパーアリーナでワンマンライブをおこなったり、『劇場版ポケットモンスター ココ』のテーマ曲を担当したりするなど、のびやかな活動をおこなう岡崎体育さんと糸井重里の対談です。岡崎さんの創作の根本にある考えについて、糸井がじっ… https://t.co/IXYGs6HcLyポケットモンスター、縮めてポモタ★BOX販売 フチピト ポケットモンスター フチにぴっとりコレクション2\nhttps://t.co/noEc

#### トレンドワードに基づくテキスト情報を整理

In [94]:
google_trend_word_text = ','.join(google_trend_word)
google_trend_word_text

'ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア'

In [95]:
google_trend_news

'...'

In [96]:
google_trend_words

'ポケモンgoログインできない\nポケモンgo不具合\nスポットライトアワー\nポケモンgo起動しない\nポケモンgo繋がらない\nポケモンgoツイッター\nポケモンgo障害\nポケモンgo開かない\nポケモンgoスポットライトアワー\nポケモンgo立ち上がらない\nポケモンgoログインできないリアルタイム\nポケモンgo通信障害\nポケモンgo障害リアルタイム\nポケモンgo不具合今\nポケモンgoリモートレイドパス\nポケモンgoサインインできない\nポケモンgo繋がらない今\nポケモンgoエラー\nポケモンgo不具合ツイッター\nポケモンgoレベル44\nポケモンgoつながらない\nポケモンgo不具合報告\nポケモンgoネットワークエラー\nポケモンgoアプリ\nポケモンgo起動しない今日'

In [97]:
news_text

'『劇場版ポケットモンスター ココ』オンラインリアル脱出ゲームの開催を記念し、映画公式サイトにて無料で遊べる謎解き企画が開催,SCRAPは、映画『劇場版ポケットモンスター ココ』とコラボしたオンラインリアル脱出ゲーム“幻のポケモンの森からの脱出”の開催を記念して、映画公式サイトにて無料で遊べる謎解き企画を公開した。'

In [98]:
twitter_text

'＼めくってラッキー‼／\n『ポケットモンスター ソード・シールド』で受け取れる、おやめいミスドの #ラッキー がもらえちゃう、「#ラッキースクラッチカード」は1,000円（税込）ごとのお買い上げで1枚ゲットできます⭐… https://t.co/b65GsoF9Myオンラインリアル脱出ゲーム×\n劇場版ポケットモンスター ココ\n「幻のポケモンの森からの脱出」\n開催記念謎解き企画\n\nキミは、ポケモン映画公式サイトに仕掛けられた💡謎💡を解けるか⁉\n\nhttps://t.co/iizmCFStWL… https://t.co/E4QV8A0EsT4日連続！フォロー＆RTすると\n「ポケットモンスター ソードまたはシールド＋エキスパンションパス」が抽選であたる🎁\n\n1日1回チャレンジしてね！\n\n1.@misterdonut_jpをフォロー\n2.12/3 11:59迄にRT\n※… https://t.co/UBK4liWOKa【アニメでのガブリアス】\nポケットモンスターダイヤモンドパールからポケットモンスターXY(2014年1月現在)まで実は何らかの形でゲスト出演で登場していたりする。\n初登場はDP編第40話RT @famitsu: 『劇場版ポケットモンスター ココ』オンラインリアル脱出ゲームの開催を記念し、映画公式サイトにて無料で遊べる謎解き企画が開催 https://t.co/9WiHvBgt8O https://t.co/8KouDyXaDf『ポケットモンスター金・銀』: ［こおりのぬけみち］で拾うことができる［わざマシン］と［ひでんマシン］を両方答えよ。--完答15点 #poke_qJR線秋葉原駅、パノラマ秋葉原「劇場版ポケットモンスター ココ」#ココ #ポケモン映画 #ooh https://t.co/WonWi0Wacwさいたまスーパーアリーナでワンマンライブをおこなったり、『劇場版ポケットモンスター ココ』のテーマ曲を担当したりするなど、のびやかな活動をおこなう岡崎体育さんと糸井重里の対談です。岡崎さんの創作の根本にある考えについて、糸井がじっ… https://t.co/IXYGs6HcLyポケットモンスター、縮めてポモタ★BOX販売 フチピト ポケットモンスター フチにぴっとりコレクション2\nhttps://t.co/noEc

#### googleトレンドのページに記載されているテキストは重みをつける（✖️3）

In [99]:
test_text = (google_trend_word_text  + google_trend_news + google_trend_words) * 3 + news_text + twitter_text

## 楽天APIで取得済みの商品リストを持ってくる

In [100]:
import pickle
import pandas as pd

In [101]:
# .pickleから著者リストを読み出し
with open('book_list_csv.pickle','rb') as f:
    book_list = pickle.load(f)

In [102]:
book_list.columns

Index(['index', 'affiliateUrl', 'author', 'authorKana', 'availability',
       'booksGenreId', 'chirayomiUrl', 'contents', 'discountPrice',
       'discountRate', 'isbn', 'itemCaption', 'itemPrice', 'itemUrl',
       'largeImageUrl', 'limitedFlag', 'listPrice', 'mediumImageUrl',
       'postageFlag', 'publisherName', 'reviewAverage', 'reviewCount',
       'salesDate', 'seriesName', 'seriesNameKana', 'size', 'smallImageUrl',
       'subTitle', 'subTitleKana', 'title', 'titleKana'],
      dtype='object')

In [103]:
test_books = book_list['title']+","+book_list['subTitle']+","+book_list['itemCaption']

In [104]:
test_books.astype(str)

0         2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第2巻 貸付けおよび貸付けに付...
1         2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第3巻 資金需要者等の保護と財...
2          2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第1巻 貸金業法および関係法令,,
3         2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第4巻 貸金業務取扱主任者資格...
4         工事担任者DD1種標準テキスト第4版,,実際の出題傾向を反映、試験本番に強い編集内容。明快な...
                                ...                        
182477    カンタレラ,義父と義兄に愛されて,母の再婚で鉄道王の娘になったシェスティーナは、義父と母、義...
182478    皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...
182479                                 機従戦姫は微笑まない,彷徨のパルティア,
182480    縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...
182481    1級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...
Length: 182482, dtype: object

In [105]:
df1 = pd.DataFrame()
df1['test'] = test_books

In [106]:
df2 = pd.DataFrame([test_text], columns=['test'])

In [107]:
df3 = df1.append(df2).reset_index()

In [108]:
df3

index                                               test
0            0  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第2巻 貸付けおよび貸付けに付...
1            1  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第3巻 資金需要者等の保護と財...
2            2   2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第1巻 貸金業法および関係法令,,
3            3  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第4巻 貸金業務取扱主任者資格...
4            4  工事担任者DD1種標準テキスト第4版,,実際の出題傾向を反映、試験本番に強い編集内容。明快な...
...        ...                                                ...
182478  182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...
182479  182479                               機従戦姫は微笑まない,彷徨のパルティア,
182480  182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...
182481  182481  1級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...
182482       0  ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア......

[182483 rows x 2 columns]

In [109]:
df1

test
0       2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第2巻 貸付けおよび貸付けに付...
1       2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第3巻 資金需要者等の保護と財...
2        2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第1巻 貸金業法および関係法令,,
3       2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第4巻 貸金業務取扱主任者資格...
4       工事担任者DD1種標準テキスト第4版,,実際の出題傾向を反映、試験本番に強い編集内容。明快な...
...                                                   ...
182477  カンタレラ,義父と義兄に愛されて,母の再婚で鉄道王の娘になったシェスティーナは、義父と母、義...
182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...
182479                               機従戦姫は微笑まない,彷徨のパルティア,
182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...
182481  1級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...

[182482 rows x 1 columns]

#### 自然言語処理

In [110]:
from sklearn import preprocessing

In [111]:
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

In [112]:
import MeCab

In [113]:
import re

In [114]:
m = MeCab.Tagger ("-Ochasen -d /usr/local/lib/mecab/dic/mecab-ipadic-neologd")

In [115]:
# nouns = [line for line in m.parse(text).splitlines()
#                if "名詞" in line.split()[-1]]

# meishi_list = []
# for str in nouns:
#     meishi_list.append(str.split()[2])

In [116]:
# あまり関係のないと思われる数字を全て0に置き換える関数
def replace_number_to_zero(text):
    changed_text = re.sub(r'[0-9]+', "0", text) #半角
    changed_text = re.sub(r'[０-９]+', "0", changed_text) #全角
    return changed_text

# 数字を0に置換
df3['review_number_to_zero'] = df3['test'].map(replace_number_to_zero)
df3.tail()

index                                               test  \
182478  182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...   
182479  182479                               機従戦姫は微笑まない,彷徨のパルティア,   
182480  182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...   
182481  182481  1級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...   
182482       0  ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア......   

                                    review_number_to_zero  
182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...  
182479                               機従戦姫は微笑まない,彷徨のパルティア,  
182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...  
182481  0級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...  
182482  ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア......

In [117]:
# 分かち書きした結果を返す関数
def leaving_space_between_words_column(text):
    
    nouns = [line for line in m.parse(text).splitlines()
               if "名詞" in line.split()[-1]]

    meishi_list = []
    for str in nouns:
        meishi_list.append(str.split()[2])
    
#     return ','.join(meishi_list)
    return ' '.join(meishi_list)

# 分かち書きしたカラムをdfに追加する
df3['lsbw'] = df3['review_number_to_zero'].map(leaving_space_between_words_column)

In [118]:
df3

index                                               test  \
0            0  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第2巻 貸付けおよび貸付けに付...   
1            1  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第3巻 資金需要者等の保護と財...   
2            2   2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第1巻 貸金業法および関係法令,,   
3            3  2020年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第4巻 貸金業務取扱主任者資格...   
4            4  工事担任者DD1種標準テキスト第4版,,実際の出題傾向を反映、試験本番に強い編集内容。明快な...   
...        ...                                                ...   
182478  182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...   
182479  182479                               機従戦姫は微笑まない,彷徨のパルティア,   
182480  182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...   
182481  182481  1級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...   
182482       0  ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア......   

                                    review_number_to_zero  \
0       0年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第0巻 貸付けおよび貸付けに付随する...   
1       0年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第0巻 資金需要者等の保護と財務およ...   
2           0年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第0巻 貸金業法および関係法令,,   
3       0年度　国家資格 貸金業務取扱主任者資格試験 受験教本 第0巻 貸金業務取扱主任者資格試験法...   
4       工事担任者DD0種標準テキスト第0版,,実際の出題傾向を反映、試験本番に強い編集内容。明快な...   
...                                                   ...   
182478  皇帝陛下と心読みの姫,,クリシュティナは、他人の心を読める力を隠してひっそりと後宮で生活して...   
182479                               機従戦姫は微笑まない,彷徨のパルティア,   
182480  縛,王子の狂愛、囚われの姫君,元婚約者で隣国の王子ルードヴィーグに攫われ、秘密の塔に監禁され...   
182481  0級建築施工管理技士［実地試験］実践問題と記述例集　第八版,,傾向を徹底分析した施工経験記述...   
182482  ポケットモンスター,Pokémon GO,iOS,ポケモンボックス ルビー&サファイア......   

                                                     lsbw  
0       0 年度 国家資格 貸金業務取扱主任者 資格試験 受験 教本 0 巻 貸し付け 貸し付け 付...  
1       0 年度 国家資格 貸金業務取扱主任者 資格試験 受験 教本 0 巻 資金需要 者 等 保護...  
2       0 年度 国家資格 貸金業務取扱主任者 資格試験 受験 教本 0 巻 貸金業法 お呼び 関係 法令  
3       0 年度 国家資格 貸金業務取扱主任者 資格試験 受験 教本 0 巻 貸金業務取扱主任者 資...  
4       工事担任者 DD 0 種 標準 テキスト 0 版 出題 傾向 反映 試験 本番 編集 内容 ...  
...                                                   ...  
182478  皇帝陛下 心 読み 姫 クリシュティナ 他人 心 力 後宮 生活 妃 たくさん 皇帝 顔 こ...  
182479                                    機 従戦 姫 彷徨 パルティア  
182480  縛 王子 狂 愛 囚われ 姫君 元 婚約者 隣国 王子 ルードヴィーグ 秘密 塔 監禁 王女...  
182481  0 級 建築施工管理技士 実地 試験 実践 問題 記述 例 集 八 版 傾向 徹底 分析 施...  
182482  ポケットモンスター ポケモンゴー iOS ポケモンボックスルビーサファイア ポケモンGO ロ...  

[182483 rows x 4 columns]

In [119]:
vectorizer = TfidfVectorizer()
X = vectorizer.fit_transform(df3['lsbw'])

In [60]:
# del X_array

In [57]:
# X_array = X.toarray()

In [120]:
X[182482]

<1x142038 sparse matrix of type '<class 'numpy.float64'>'
	with 128 stored elements in Compressed Sparse Row format>

In [58]:
# ans = X_array[182482]

In [121]:
from sklearn.metrics.pairwise import cosine_similarity

In [122]:
similarity = cosine_similarity(X[182482], X)

In [123]:
aaa = similarity[0].tolist()

In [133]:
sorted(aaa)[-5]

0.06008268335093912

In [134]:
# maxとlist.indexによる実装
max_value = sorted(aaa)[-6]
max_index = aaa.index(max_value)
print(max_index)

116265


In [126]:
df3.iloc[161730, :]

index                                                               161730
test                     ポケモンGOは終わらない,,本当に笑っているのは誰か？語られざる「ポケノミクス」の正体！リリ...
review_number_to_zero    ポケモンGOは終わらない,,本当に笑っているのは誰か？語られざる「ポケノミクス」の正体！リリ...
lsbw                     ポケモンGO の 誰か Pokenomics 正体 リリース 以来 世界 席巻 Pokemo...
Name: 161730, dtype: object

In [128]:
df3.iloc[174879, :]

index                               174879
test                     劇場版ポケットモンスター　ココ,,
review_number_to_zero    劇場版ポケットモンスター　ココ,,
lsbw                       劇場版ポケットモンスター ココ
Name: 174879, dtype: object

In [130]:
df3.iloc[174866, :]

index                                  174866
test                     ポケットモンスターB・W編（第1巻）,,
review_number_to_zero    ポケットモンスターB・W編（第0巻）,,
lsbw                      ポケットモンスター B W 編 0 巻
Name: 174866, dtype: object

In [2]:
book_list.column

NameError: name 'book_list' is not defined

In [138]:
book_list.loc[[161730,174879, 174866],:]

index affiliateUrl               author                   authorKana  \
161730  230774                             西田宗千佳                     ニシダ,ムネチカ   
174879  248035                水野輝昭/小学館集英社プロダクション                                
174866  248022               穴久保幸作/小学館集英社プロダクション  アナクボ,コウサク/シヨウガクカンシユウエイシヤプロダ   

       availability                      booksGenreId chirayomiUrl contents  \
161730            1  001011005001/001020008/001020014                         
174879            5                      001001001014                         
174866            1                            001015                         

        discountPrice  discountRate  ... reviewCount     salesDate  \
161730              0             0  ...           3      2016年11月   
174879              0             0  ...           0  2020年12月25日頃   
174866              0             0  ...           0   2011年08月26日   

        seriesName seriesNameKana  size  \
161730        朝日新書       アサヒ シンショ    新書   
174879  てんとう虫コミックス                 コミック   
174866   コロコロコミックス                 コミック   

                                            smallImageUrl  subTitle  \
161730  https://thumbnail.image.rakuten.co.jp/@0_mall/...             
174879  https://thumbnail.image.rakuten.co.jp/@0_mall/...             
174866  https://thumbnail.image.rakuten.co.jp/@0_mall/...             

       subTitleKana               title               titleKana  
161730                     ポケモンGOは終わらない         ポケモン ゴー ワ オワラナイ  
174879                  劇場版ポケットモンスター　ココ         劇場版ポケットモンスター　ココ  
174866               ポケットモンスターB・W編（第1巻）  ポケット モンスター ブラック ホワイトヘン  

[3 rows x 31 columns]

In [304]:
# 各文章の重要度を確認するコード
# print('feature_names:', vectorizer.get_feature_names())
# words = vectorizer.get_feature_names()
# for doc_id, vec in zip(range(len(df3['lsbw'])), X.toarray()):
#     print('doc_id:', doc_id)
#     for w_id, tfidf in sorted(enumerate(vec), key=lambda x: x[1], reverse=True):
#         lemma = words[w_id]
#         print('\t{0:s}: {1:f}'.format(lemma, tfidf))

feature_names: ['01', '04', '0cm', '0g', '0kg', '0km', '0m', '0mm', '0t', '0v', '0verflow', '0w', '0インチ', '0キロ', '0セント', '0タイプ', '0ドル', '0パーセント', '0マン', '0件', '0倍', '0円', '0分', '0回', '0回目', '0回転', '0基', '0学占い', '0安打', '0度', '0打', '0時', '0本', '0次会', '0歳', '0点', '0秒', '0種類', '0系', '0系新幹線', '0部', '0階', '0階建て', '10', '100000人', '100000円', '10000人', '10000円', '10000回', '10000枚', '1000m', '1000キロ', '1000ドル', '1000万人', '1000倍', '1000兆円', '1000回', '1000点', '1001', '100キロ', '100パーセント', '100万人', '100万円', '100倍', '100億円', '100周年', '100回', '100年', '100年前', '100年後', '100年間', '100日', '100日間', '100期', '100枚', '100点', '100番', '100話', '101年', '102', '1020', '103歳', '10412', '1060', '1066', '1080', '10re', '10か月', '10キロ', '10世紀', '10代前半', '10代目', '10件', '10億円', '10円', '10周', '10回', '10巻', '10年', '10年前', '10年後', '10年間', '10日目', '10日間', '10時間', '10曲', '10月10日', '10月13日', '10月15日', '10月下旬', '10本', '10歳', '10秒', '10級', '1100年', '11494', '1156', '1159', '1163', '11980', '11か月', '11世紀', '11人', '11代', '11代目', 

doc_id: 0
	貸し付け: 0.649414
	付随: 0.313079
	貸金業務取扱主任者: 0.307324
	国家資格: 0.298430
	資格試験: 0.259646
	取引: 0.226852
	法令: 0.218327
	教本: 0.206505
	実務: 0.197359
	受験: 0.176267
	年度: 0.132382
	01: 0.000000
	04: 0.000000
	0cm: 0.000000
	0g: 0.000000
	0kg: 0.000000
	0km: 0.000000
	0m: 0.000000
	0mm: 0.000000
	0t: 0.000000
	0v: 0.000000
	0verflow: 0.000000
	0w: 0.000000
	0インチ: 0.000000
	0キロ: 0.000000
	0セント: 0.000000
	0タイプ: 0.000000
	0ドル: 0.000000
	0パーセント: 0.000000
	0マン: 0.000000
	0件: 0.000000
	0倍: 0.000000
	0円: 0.000000
	0分: 0.000000
	0回: 0.000000
	0回目: 0.000000
	0回転: 0.000000
	0基: 0.000000
	0学占い: 0.000000
	0安打: 0.000000
	0度: 0.000000
	0打: 0.000000
	0時: 0.000000
	0本: 0.000000
	0次会: 0.000000
	0歳: 0.000000
	0点: 0.000000
	0秒: 0.000000
	0種類: 0.000000
	0系: 0.000000
	0系新幹線: 0.000000
	0部: 0.000000
	0階: 0.000000
	0階建て: 0.000000
	10: 0.000000
	100000人: 0.000000
	100000円: 0.000000
	10000人: 0.000000
	10000円: 0.000000
	10000回: 0.000000
	10000枚: 0.000000
	1000m: 0.000000
	1000キロ: 0.000000
	1000ドル: 0.000000
	1000万人: 

	97歳: 0.000000
	98人: 0.000000
	98期: 0.000000
	99人: 0.000000
	99勝: 0.000000
	99階: 0.000000
	9mm: 0.000000
	9か月: 0.000000
	9パーセント: 0.000000
	9世紀: 0.000000
	9人: 0.000000
	9代: 0.000000
	9代目: 0.000000
	9億円: 0.000000
	9割: 0.000000
	9回: 0.000000
	9基: 0.000000
	9巻: 0.000000
	9年: 0.000000
	9年前: 0.000000
	9年間: 0.000000
	9敗: 0.000000
	9日間: 0.000000
	9月15日: 0.000000
	9月1日: 0.000000
	9月24日: 0.000000
	9月26日: 0.000000
	9月5日: 0.000000
	9月8日: 0.000000
	9月下旬: 0.000000
	9歳: 0.000000
	a0サイズ: 0.000000
	aa: 0.000000
	aaa: 0.000000
	aap: 0.000000
	ab: 0.000000
	aba: 0.000000
	abandoned: 0.000000
	abbado: 0.000000
	abby: 0.000000
	abc: 0.000000
	abcde: 0.000000
	abcdes: 0.000000
	abcs: 0.000000
	abc殺人事件: 0.000000
	abe: 0.000000
	abec: 0.000000
	abeille: 0.000000
	abel: 0.000000
	abend: 0.000000
	abenomics: 0.000000
	ability: 0.000000
	abis: 0.000000
	abl: 0.000000
	ableton: 0.000000
	about: 0.000000
	abridged: 0.000000
	absolute: 0.000000
	abx: 0.000000
	abyss: 0.000000
	ab型: 0.000000
	ac: 0.000000
	academic:

	biscuit: 0.000000
	bisesi: 0.000000
	biske: 0.000000
	bisque: 0.000000
	bit: 0.000000
	bitcoin: 0.000000
	bite: 0.000000
	bito: 0.000000
	bitsch: 0.000000
	bitter: 0.000000
	bitzan: 0.000000
	biutifulビューティフル: 0.000000
	biz: 0.000000
	bizarre: 0.000000
	bj: 0.000000
	bjt: 0.000000
	bk: 0.000000
	bl: 0.000000
	bla: 0.000000
	blabo: 0.000000
	black: 0.000000
	blackie: 0.000000
	blackish: 0.000000
	blackout: 0.000000
	blacks: 0.000000
	blade: 0.000000
	blaive: 0.000000
	blame: 0.000000
	blanc: 0.000000
	blanche: 0.000000
	blancpain: 0.000000
	blanken: 0.000000
	blankenburg: 0.000000
	blant: 0.000000
	blas: 0.000000
	blast: 0.000000
	blaster: 0.000000
	blaut: 0.000000
	blaze: 0.000000
	blazek: 0.000000
	blazing: 0.000000
	bleach: 0.000000
	blend: 0.000000
	blenda: 0.000000
	blender: 0.000000
	bless: 0.000000
	blessed: 0.000000
	blessing: 0.000000
	bleu: 0.000000
	bleue: 0.000000
	bli: 0.000000
	blind: 0.000000
	bliss: 0.000000
	block: 0.000000
	blockchain: 0.000000
	blocks: 0.000000
	block

	cg: 0.000000
	cgi: 0.000000
	cgworld: 0.000000
	ch: 0.000000
	cha: 0.000000
	chab: 0.000000
	chaba: 0.000000
	chado: 0.000000
	chagu: 0.000000
	chain: 0.000000
	chainer: 0.000000
	chakra: 0.000000
	chakura: 0.000000
	challen: 0.000000
	challenge: 0.000000
	chamber: 0.000000
	champ: 0.000000
	chan: 0.000000
	chance: 0.000000
	chandler: 0.000000
	change: 0.000000
	changes: 0.000000
	changing: 0.000000
	channel: 0.000000
	channelbay: 0.000000
	chano: 0.000000
	chansons: 0.000000
	chantal: 0.000000
	chante: 0.000000
	chaos: 0.000000
	chap: 0.000000
	chappie: 0.000000
	chapter: 0.000000
	char: 0.000000
	character: 0.000000
	characteristiques: 0.000000
	characters: 0.000000
	charge: 0.000000
	charles: 0.000000
	charlie: 0.000000
	charlotte: 0.000000
	chart: 0.000000
	chase: 0.000000
	chasin: 0.000000
	chatterbox: 0.000000
	chatwork: 0.000000
	chaya: 0.000000
	chdf: 0.000000
	cheap: 0.000000
	cheat: 0.000000
	check: 0.000000
	checkmate: 0.000000
	cheer: 0.000000
	cheers: 0.000000
	cheerz: 0.

...

	羽瑠: 0.000000
	羽生: 0.000000
	羽生マジック: 0.000000
	羽生世代: 0.000000
	羽生善治: 0.000000
	羽生田栄一: 0.000000
	羽生結弦: 0.000000
	羽田: 0.000000
	羽田五郎: 0.000000
	羽田圭介: 0.000000
	羽田秀吉: 0.000000
	羽田空港: 0.000000
	羽田美智子: 0.000000
	羽目: 0.000000
	羽矢: 0.000000
	羽箒: 0.000000
	羽織: 0.000000
	羽織り: 0.000000
	羽虫: 0.000000
	羽衣: 0.000000
	羽衣伝説: 0.000000
	羽角: 0.000000
	羽賀朱音: 0.000000
	羽越本線: 0.000000
	羽野: 0.000000
	羽音: 0.000000
	羽黒: 0.000000
	羽黒山: 0.000000
	翌々年: 0.000000
	翌々日: 0.000000
	翌年: 0.000000
	翌日: 0.000000
	翌月: 0.000000
	翌朝: 0.000000
	翌週: 0.000000
	習い: 0.000000
	習い事: 0.000000
	習うより慣れろ: 0.000000
	習わし: 0.000000
	習作: 0.000000
	習俗: 0.000000
	習合: 0.000000
	習字: 0.000000
	習得: 0.000000
	習志野: 0.000000
	習志野市: 0.000000
	習性: 0.000000
	習慣: 0.000000
	習慣病: 0.000000
	習熟: 0.000000
	習練: 0.000000
	習近平: 0.000000
	習近平体制: 0.000000
	翔ぶが如く: 0.000000
	翔一: 0.000000
	翔也: 0.000000
	翔二: 0.000000
	翔介: 0.000000
	翔吾: 0.000000
	翔和学園: 0.000000
	翔哉: 0.000000
	翔多: 0.000000
	翔太: 0.000000
	翔太郎: 0.000000
	翔子: 0.000000
	翔平: 0.000000
	翔泳社: 0.000000
	翔田寛: 

	自分のために: 0.000000
	自分の説明書: 0.000000
	自分は自分: 0.000000
	自分らしさ: 0.000000
	自分を棚に上げる: 0.000000
	自分を高める: 0.000000
	自分ルール: 0.000000
	自分勝手: 0.000000
	自分史: 0.000000
	自分年金: 0.000000
	自分探し: 0.000000
	自分磨き: 0.000000
	自分自身: 0.000000
	自分語り: 0.000000
	自刎: 0.000000
	自制: 0.000000
	自制心: 0.000000
	自前: 0.000000
	自力: 0.000000
	自力救済: 0.000000
	自助: 0.000000
	自助グループ: 0.000000
	自助努力: 0.000000
	自助論: 0.000000
	自動: 0.000000
	自動ブレーキ: 0.000000
	自動人形: 0.000000
	自動体外式除細動器: 0.000000
	自動化: 0.000000
	自動売買: 0.000000
	自動操縦: 0.000000
	自動機: 0.000000
	自動的: 0.000000
	自動詞: 0.000000
	自動認識: 0.000000
	自動販売機: 0.000000
	自動車: 0.000000
	自動車メーカー: 0.000000
	自動車事故: 0.000000
	自動車保険: 0.000000
	自動車工学: 0.000000
	自動車教習所: 0.000000
	自動車整備士: 0.000000
	自動車整備工場: 0.000000
	自動車業界: 0.000000
	自動車爆弾: 0.000000
	自動車産業: 0.000000
	自動車評論: 0.000000
	自動車販売: 0.000000
	自動車部品: 0.000000
	自動車雑誌: 0.000000
	自動運転: 0.000000
	自動運転技術: 0.000000
	自動運転車: 0.000000
	自叙伝: 0.000000
	自叙帖: 0.000000
	自問: 0.000000
	自問自答: 0.000000
	自営: 0.000000
	自営業: 0.000000
	自嘲: 0.000000
	自国: 0.

	花芽: 0.000000
	花苗: 0.000000
	花菖蒲: 0.000000
	花菜: 0.000000
	花菱: 0.000000
	花落: 0.000000
	花葬: 0.000000
	花蓮: 0.000000
	花蕾: 0.000000
	花蘇芳: 0.000000
	花蘭: 0.000000
	花街: 0.000000
	花衣: 0.000000
	花袋: 0.000000
	花見: 0.000000
	花見堂: 0.000000
	花見客: 0.000000
	花見酒: 0.000000
	花言葉: 0.000000
	花詩集: 0.000000
	花譜: 0.000000
	花賀: 0.000000
	花輪: 0.000000
	花輪クン: 0.000000
	花道: 0.000000
	花邑: 0.000000
	花里: 0.000000
	花野: 0.000000
	花野井: 0.000000
	花鏡: 0.000000
	花開: 0.000000
	花陽: 0.000000
	花電車: 0.000000
	花音: 0.000000
	花香: 0.000000
	花骨牌: 0.000000
	花魁: 0.000000
	花鳥: 0.000000
	花鳥画: 0.000000
	花鳥諷詠: 0.000000
	花鳥風月: 0.000000
	芳三郎: 0.000000
	芳乃: 0.000000
	芳佳: 0.000000
	芳元: 0.000000
	芳光: 0.000000
	芳典: 0.000000
	芳凛: 0.000000
	芳名: 0.000000
	芳国: 0.000000
	芳子: 0.000000
	芳山和子: 0.000000
	芳川: 0.000000
	芳年: 0.000000
	芳恵: 0.000000
	芳文: 0.000000
	芳昭: 0.000000
	芳晴: 0.000000
	芳木: 0.000000
	芳村: 0.000000
	芳林: 0.000000
	芳樹: 0.000000
	芳次郎: 0.000000
	芳烈: 0.000000
	芳田: 0.000000
	芳町: 0.000000
	芳秀: 0.000000
	芳紀: 0.000000
	芳藤: 0.000000
	芳谷: 0.000000

	萩本: 0.000000
	萩焼: 0.000000
	萩谷: 0.000000
	萩野: 0.000000
	萬世: 0.000000
	萬吉: 0.000000
	萬子: 0.000000
	萬宝: 0.000000
	萬屋: 0.000000
	萬年: 0.000000
	萬斎: 0.000000
	萬津: 0.000000
	萬田: 0.000000
	萬画: 0.000000
	萬福: 0.000000
	萬福寺: 0.000000
	萬葉: 0.000000
	萬葉集: 0.000000
	萬里: 0.000000
	萬願寺: 0.000000
	萱森: 0.000000
	萱草: 0.000000
	萱野: 0.000000
	落し: 0.000000
	落しもの: 0.000000
	落し文: 0.000000
	落し物: 0.000000
	落し穴: 0.000000
	落し紙: 0.000000
	落ち: 0.000000
	落ちこぼれ: 0.000000
	落ちゆく: 0.000000
	落ち度: 0.000000
	落ち梅記: 0.000000
	落ち武者: 0.000000
	落ち物パズル: 0.000000
	落ち目: 0.000000
	落ち着き: 0.000000
	落ち葉: 0.000000
	落ち込み: 0.000000
	落とし: 0.000000
	落とし主: 0.000000
	落とし前: 0.000000
	落とし物: 0.000000
	落とし穴: 0.000000
	落下: 0.000000
	落下する夕方: 0.000000
	落下傘: 0.000000
	落人: 0.000000
	落伍: 0.000000
	落伍者: 0.000000
	落合: 0.000000
	落合博満: 0.000000
	落合陽一: 0.000000
	落命: 0.000000
	落城: 0.000000
	落差: 0.000000
	落成: 0.000000
	落日: 0.000000
	落日燃ゆ: 0.000000
	落書: 0.000000
	落書き: 0.000000
	落札: 0.000000
	落果: 0.000000
	落武者: 0.000000
	落涙: 0.000000
	落盤: 0.000000
	落着: 0.000

KeyboardInterrupt: 